# DESERCION DE EMPLEADOS

### PROBLEMA
 La deserción de empleados en las empresas (employee attrition) es un aspecto inevitable debido a variadas razones. Por ejemplo, el retiro puede obedecer a una actualización de conocimientos (estudios) que abre otras oportunidades para el trabajador; a razones familiares que impliquen mudarse lejos del lugar de trabajo; imperativos de salud y el haber cumplido con los requisitos para
optar a la jubilación. Es decir, la disminución de una plantilla de empleados no obedece necesariamente a que aquellos tengan problemas con su empleador, sino que puede responder a factores relacionados con las condiciones y desarrollos de vida de cada uno. Sin embargo, para las empresas sería de gran valor identificar con suficiente antelación los empleados que podrían considerar el abandono de sus puestos de trabajo y los factores relacionados con estas decisiones.

### OBJETIVO
Utilizar un algoritmo de basado en combinación de clasificadores (Ensembles) para la estimación de este modelo de predicción. Identificar las variables más importantes para el problema. Nota: utilice el conjunto de datos preparado en del Taller 1.

###  CONJUNTO DE DATOS
se localizan en la carpeta local "/data" para facil lectura en otros computadores.
 - IBM-Employee-Attrition.csv

In [1]:
# importando dependencias de trabajo
# facilitar el trabajo en Jupyter
# from IPython.core.interactiveshell import InteractiveShell
# InteractiveShell.ast_node_interactivity = "all"

# se importa OS, pandas y numpy para leer y preparar datos
import os
from collections import OrderedDict
from collections import Counter
import pandas as pd
from pandas import ExcelWriter
from pandas import ExcelFile
import pandas_profiling as profile
import numpy as np

# los modelos de aprendizaje son
from sklearn.ensemble import RandomForestClassifier

# sklearn para manejo de experimentos, pruebas, optimizacion y otros
from sklearn.model_selection import train_test_split
from sklearn.metrics import confusion_matrix
from sklearn.metrics import classification_report
from sklearn.model_selection import cross_val_score
from sklearn.metrics import accuracy_score
from sklearn.metrics import precision_score
from sklearn.metrics import make_scorer
from sklearn.model_selection import GridSearchCV
from imblearn.over_sampling import SMOTE

### Cargar archivos

Se carga y se prueba disponibilidad del archivo "IBM-Employee-Attrition.csv".

In [2]:
# se cargan por medio de un path abstracto
# definiendo los nombres del archivo de datos para entrenamiento
# archivo de entrenamiento
sourceFile = os.path.join("data", "IBM-Employee-Attrition.csv")
sourceData = pd.read_csv(os.path.join(os.getcwd(), sourceFile), sep = ',', engine = 'python')

In [3]:
# probando que el archivo de entrenamiento carga
sourceData.head()

ï»¿Age Attrition     BusinessTravel  DailyRate              Department  \
0      41       Yes      Travel_Rarely       1102                   Sales   
1      49        No  Travel_Frequently        279  Research & Development   
2      37       Yes      Travel_Rarely       1373  Research & Development   
3      33        No  Travel_Frequently       1392  Research & Development   
4      27        No      Travel_Rarely        591  Research & Development   

   DistanceFromHome  Education EducationField  EmployeeCount  EmployeeNumber  \
0                 1          2  Life Sciences              1               1   
1                 8          1  Life Sciences              1               2   
2                 2          2          Other              1               4   
3                 3          4  Life Sciences              1               5   
4                 2          1        Medical              1               7   

   ...  RelationshipSatisfaction StandardHours  StockOptionLevel  \
0  ...                         1            80                 0   
1  ...                         4            80                 1   
2  ...                         2            80                 0   
3  ...                         3            80                 0   
4  ...                         4            80                 1   

   TotalWorkingYears  TrainingTimesLastYear WorkLifeBalance  YearsAtCompany  \
0                  8                      0               1               6   
1                 10                      3               3              10   
2                  7                      3               3               0   
3                  8                      3               3               8   
4                  6                      3               3               2   

  YearsInCurrentRole  YearsSinceLastPromotion  YearsWithCurrManager  
0                  4                        0                     5  
1                  7                        1                     7  
2                  0                        0                     0  
3                  7                        3                     0  
4                  2                        2                     2  

[5 rows x 35 columns]

### Análisis Preliminar De Datos

Se realiza un análisis preliminar con pandas_profile. Luego, se preparan los nombres de las columnas del conjunto de dato y se modifican para evitar confusiones en el procesamiento.

Se revisa si se necesita hacer alguna conversión del tipo de las columnas para mejorar el tiempo de procesamiento o simplificar el modelo de aprendizaje . Por último, el informe de pandas_profile ayuda a identificar las columnas innecesarias o que entorpezcan el entrenamiento.

In [4]:
# nombres de las columans del archivo "IBM-Employee-Attrition.cvs"
sourceColumnNames = list(sourceData)
# como existe algo raro en la columna de edad con tag "ï»¿Age", se renombra a "Age" para facilidad de procesamiento.
sourceData.dtypes

ï»¿Age                       int64
Attrition                   object
BusinessTravel              object
DailyRate                    int64
Department                  object
DistanceFromHome             int64
Education                    int64
EducationField              object
EmployeeCount                int64
EmployeeNumber               int64
EnvironmentSatisfaction      int64
Gender                      object
HourlyRate                   int64
JobInvolvement               int64
JobLevel                     int64
JobRole                     object
JobSatisfaction              int64
MaritalStatus               object
MonthlyIncome                int64
MonthlyRate                  int64
NumCompaniesWorked           int64
Over18                      object
OverTime                    object
PercentSalaryHike            int64
PerformanceRating            int64
RelationshipSatisfaction     int64
StandardHours                int64
StockOptionLevel             int64
TotalWorkingYears   

### Reporte del análisis

In [5]:
# chequeo los datos
profile.ProfileReport(sourceData)

### Modificaciones al conjunto de datos despues de analisis

Despues del analisis de datos, se toman las siguientes decisiones:

- La columna "EmployeeCount" se rechaza porque es constante en todo su rango.
- La columna "EmployeeNumber" se rechaza porque es el ID que entorpece el entrenamiento.
- Las columnas "MonthlyIncome" y "JobLevel" estan fuertemente correlacionadas, se selecciona (ρ = 0.9502999135). "JobLevel" como unica columna para entrenar y porque simplifica el modelo.
- La columna "Over18" se rechaza porque es constante en todo su rango.
- La columna "StandardHours" se rechaza porque es constante en todo su rango.
- Las columnas "NumCompaniesWorked", "TrainingTimesLastYear", "YearsAtCompany", "YearsInCurrentRole", "YearsSinceLastPromotion", "YearsWithCurrManager" tiene ceros (0) en su rango, sin embargo son parte del fenomeno porque existen empleados que hasta ahora tienen su primer empleo, esto hace que los datos tengan sentido y deban tenerse en cuenta.
- La columna "Attrition" es la variable que yo quiero predecir con el modelo entrenado.

In [6]:
# sacando del conjunto de datos las columnas que estan muy correlacionadas o entorpecen el entrenamiento
rejectedColumns = [
    "EmployeeCount", 
    "EmployeeNumber",
    "MonthlyIncome",
    "Over18",
    "StandardHours",
]

# como existe algo raro en la columna de edad con tag "ï»¿Age", se renombra a "Age" para facilidad de procesamiento.
# nombres viejos de las columnas
oldColumnNames = [
    "ï»¿Age", 
]
# nombres nuevos de las columnas por facilidad
newColumnNames = [
    "Age",
]

In [7]:
# se asegura no intentar borrar o modificar una columna que ya se borro o se modifico en el XSLX y el CSV.
# se inicia con el archivo CSV
sourceColumnNames = list(sourceData)

for column in rejectedColumns:
    if column in sourceColumnNames:
        # se elimina la columna que todavia no se ha borrado
        sourceData = sourceData.drop(columns = column, axis = 1)     

sourceColumnNames = list(sourceData)
# diccionario para renombrar columnas en pandas
renameDictCol = dict()
     
# renombrar columnas en el CSV para facilidad
for old, new in zip(oldColumnNames, newColumnNames):
    if old in sourceColumnNames:
        renameDictCol[old] = new
    sourceData = sourceData.rename(columns = renameDictCol)
    sourceColumnNames = list(sourceData)

In [8]:
# chequeando como va el CSV   
sourceData.dtypes

Age                          int64
Attrition                   object
BusinessTravel              object
DailyRate                    int64
Department                  object
DistanceFromHome             int64
Education                    int64
EducationField              object
EnvironmentSatisfaction      int64
Gender                      object
HourlyRate                   int64
JobInvolvement               int64
JobLevel                     int64
JobRole                     object
JobSatisfaction              int64
MaritalStatus               object
MonthlyRate                  int64
NumCompaniesWorked           int64
OverTime                    object
PercentSalaryHike            int64
PerformanceRating            int64
RelationshipSatisfaction     int64
StockOptionLevel             int64
TotalWorkingYears            int64
TrainingTimesLastYear        int64
WorkLifeBalance              int64
YearsAtCompany               int64
YearsInCurrentRole           int64
YearsSinceLastPromot

### Cambio del Tipo de Columnas
se detectan diferentes columnas con tipo de datos “object”, es necesario cambiar el tipo de dato a “int64”. Para ello se crea un diccionario de transformación creado con los valores únicos presentes en cada columna con su equivalente en números enteros.

No se hace necesario una discretización de las variables porque el comportamiento del fenómeno se abstraería mucho y podría perderse precisión.

In [9]:
# utilizando datypes saco cuales son las columnas con objetos para transformarlas a numeros
objectColumnList = list()

for cname, dtype in zip(list(sourceData), sourceData.dtypes):
    if dtype == "object":
#         print(cname, dtype)
        objectColumnList.append(cname)
#         sourceData[cname].astype("int64")
print("--- Lista de Columnas para Cambio de Tipo ---")
print(objectColumnList)

--- Lista de Columnas para Cambio de Tipo ---
['Attrition', 'BusinessTravel', 'Department', 'EducationField', 'Gender', 'JobRole', 'MaritalStatus', 'OverTime']


In [10]:
# creando el diccionario de transformacion de las columnas categoricas en numricas
transformationDict = dict()

for cname in objectColumnList:
    
    if len(objectColumnList) != len(transformationDict.keys()):
    
        tempCategory = list(sourceData[cname].unique())
        tempCategory.sort()
        tempNumeric = list(np.linspace(0, len(tempCategory)-1, len(tempCategory), dtype = "int64"))

        for numeric, category in zip(tempNumeric, tempCategory):
    #         print(numeric, category)
            transformationDict[cname] = dict()

        for numeric, category in zip(tempNumeric, tempCategory):
    #         print(numeric, category)
            transformationDict[cname][category] = numeric

print("--- Diccionario de Equivalencias para las Columnas ---")
for key in transformationDict:
    print(str(key) + ": \n" + str(transformationDict[key]))

--- Diccionario de Equivalencias para las Columnas ---
Attrition: 
{'No': 0, 'Yes': 1}
BusinessTravel: 
{'Non-Travel': 0, 'Travel_Frequently': 1, 'Travel_Rarely': 2}
Department: 
{'Human Resources': 0, 'Research & Development': 1, 'Sales': 2}
EducationField: 
{'Human Resources': 0, 'Life Sciences': 1, 'Marketing': 2, 'Medical': 3, 'Other': 4, 'Technical Degree': 5}
Gender: 
{'Female': 0, 'Male': 1}
JobRole: 
{'Healthcare Representative': 0, 'Human Resources': 1, 'Laboratory Technician': 2, 'Manager': 3, 'Manufacturing Director': 4, 'Research Director': 5, 'Research Scientist': 6, 'Sales Executive': 7, 'Sales Representative': 8}
MaritalStatus: 
{'Divorced': 0, 'Married': 1, 'Single': 2}
OverTime: 
{'No': 0, 'Yes': 1}


In [11]:
# cambiando los valores de las categoricas a numericas para proceder con el dummy
for cname in objectColumnList:
    newDataColumn = list()
    
    # si esta en el diccionario y es de tipo objeto se cambia el tipo de dato
    if cname in transformationDict.keys() and sourceData[cname].dtype == "object":
#         print(cname)
        for i in range (0, len(sourceData[cname])):
#             print(sourceData[cname][i])
#             print(transformationDict[cname][sourceData[cname][i]])
            newDataColumn.append(transformationDict[cname][sourceData[cname][i]])
                
        sourceData[cname] = newDataColumn
        sourceData.astype({cname:"int64"})

In [12]:
# recisando el cambio de typos en las columnas
sourceData.dtypes

Age                         int64
Attrition                   int64
BusinessTravel              int64
DailyRate                   int64
Department                  int64
DistanceFromHome            int64
Education                   int64
EducationField              int64
EnvironmentSatisfaction     int64
Gender                      int64
HourlyRate                  int64
JobInvolvement              int64
JobLevel                    int64
JobRole                     int64
JobSatisfaction             int64
MaritalStatus               int64
MonthlyRate                 int64
NumCompaniesWorked          int64
OverTime                    int64
PercentSalaryHike           int64
PerformanceRating           int64
RelationshipSatisfaction    int64
StockOptionLevel            int64
TotalWorkingYears           int64
TrainingTimesLastYear       int64
WorkLifeBalance             int64
YearsAtCompany              int64
YearsInCurrentRole          int64
YearsSinceLastPromotion     int64
YearsWithCurrM

In [13]:
sourceData.head()

Age  Attrition  BusinessTravel  DailyRate  Department  DistanceFromHome  \
0   41          1               2       1102           2                 1   
1   49          0               1        279           1                 8   
2   37          1               2       1373           1                 2   
3   33          0               1       1392           1                 3   
4   27          0               2        591           1                 2   

   Education  EducationField  EnvironmentSatisfaction  Gender  ...  \
0          2               1                        2       0  ...   
1          1               1                        3       1  ...   
2          2               4                        4       1  ...   
3          4               1                        4       0  ...   
4          1               3                        1       1  ...   

   PerformanceRating  RelationshipSatisfaction  StockOptionLevel  \
0                  3                         1                 0   
1                  4                         4                 1   
2                  3                         2                 0   
3                  3                         3                 0   
4                  3                         4                 1   

   TotalWorkingYears  TrainingTimesLastYear  WorkLifeBalance  YearsAtCompany  \
0                  8                      0                1               6   
1                 10                      3                3              10   
2                  7                      3                3               0   
3                  8                      3                3               8   
4                  6                      3                3               2   

   YearsInCurrentRole  YearsSinceLastPromotion  YearsWithCurrManager  
0                   4                        0                     5  
1                   7                        1                     7  
2                   0                        0                     0  
3                   7                        3                     0  
4                   2                        2                     2  

[5 rows x 30 columns]

### Creando Representación Alterna
En esta etapa represento alternativamente los datos para facilitar el entrenamiento del modelo y retiro los datos que están fuera del rango y no representan el fenómeno.

In [14]:
# fijando las columnas que transformare en dummies
dummyColumnNames = sourceColumnNames

if "Attrition" in dummyColumnNames:
    dummyColumnNames.pop(dummyColumnNames.index("Attrition"))
dummyColumnNames

['Age',
 'BusinessTravel',
 'DailyRate',
 'Department',
 'DistanceFromHome',
 'Education',
 'EducationField',
 'EnvironmentSatisfaction',
 'Gender',
 'HourlyRate',
 'JobInvolvement',
 'JobLevel',
 'JobRole',
 'JobSatisfaction',
 'MaritalStatus',
 'MonthlyRate',
 'NumCompaniesWorked',
 'OverTime',
 'PercentSalaryHike',
 'PerformanceRating',
 'RelationshipSatisfaction',
 'StockOptionLevel',
 'TotalWorkingYears',
 'TrainingTimesLastYear',
 'WorkLifeBalance',
 'YearsAtCompany',
 'YearsInCurrentRole',
 'YearsSinceLastPromotion',
 'YearsWithCurrManager']

In [15]:
# creando la matriz de datos con dummies
sourceDataDummies = pd.get_dummies(sourceData, columns = dummyColumnNames)
sourceDataDummies.dtypes

Attrition                  int64
Age_18                     uint8
Age_19                     uint8
Age_20                     uint8
Age_21                     uint8
                           ...  
YearsWithCurrManager_13    uint8
YearsWithCurrManager_14    uint8
YearsWithCurrManager_15    uint8
YearsWithCurrManager_16    uint8
YearsWithCurrManager_17    uint8
Length: 2683, dtype: object

In [16]:
#confirmando operaciones
sourceDataDummies.head()

Attrition  Age_18  Age_19  Age_20  Age_21  Age_22  Age_23  Age_24  Age_25  \
0          1       0       0       0       0       0       0       0       0   
1          0       0       0       0       0       0       0       0       0   
2          1       0       0       0       0       0       0       0       0   
3          0       0       0       0       0       0       0       0       0   
4          0       0       0       0       0       0       0       0       0   

   Age_26  ...  YearsWithCurrManager_8  YearsWithCurrManager_9  \
0       0  ...                       0                       0   
1       0  ...                       0                       0   
2       0  ...                       0                       0   
3       0  ...                       0                       0   
4       0  ...                       0                       0   

   YearsWithCurrManager_10  YearsWithCurrManager_11  YearsWithCurrManager_12  \
0                        0                        0                        0   
1                        0                        0                        0   
2                        0                        0                        0   
3                        0                        0                        0   
4                        0                        0                        0   

   YearsWithCurrManager_13  YearsWithCurrManager_14  YearsWithCurrManager_15  \
0                        0                        0                        0   
1                        0                        0                        0   
2                        0                        0                        0   
3                        0                        0                        0   
4                        0                        0                        0   

   YearsWithCurrManager_16  YearsWithCurrManager_17  
0                        0                        0  
1                        0                        0  
2                        0                        0  
3                        0                        0  
4                        0                        0  

[5 rows x 2683 columns]

### División de Datos para el Entrenamiento

La clase de atrición en la columna “Attrition” esta desbalanceada y para minimizar errores se utiliza el método de balanceo del entrenamiento de datos por SMOTE para aumentar la población de las diferentes clases (en este caso “Yes:1” o “No:0”) y mejorar el rendimiento del modelo de predicción.

Para completar esta tarea se utiliza una clase especializada, y no se debe olvidar el comando "pip install imbalanced-learn" para utilizar SMOTE en el conjunto de datos.

In [17]:
# chequeando los tipos de severidad para ver si necesita balanceo
sourceDataDummies["Attrition"].value_counts()

0    1233
1     237
Name: Attrition, dtype: int64

In [18]:
# conjunto de entrenamiento sin balancear
trainData = sourceDataDummies
trainDataBalance = pd.DataFrame()

In [19]:
# conjunto de entrenamiento entrenado
# las clases 1 y 2 necesitan un sobre muestreo del mismo orden de magnitud que la clase 3
# con SMOTE porque es cool y 42 la respuesta universal de HHGttG
smoteResampler = SMOTE(random_state = 42)
dummyColumnNames = list(sourceDataDummies.drop(columns = ["Attrition"], axis = 1))
smX, smY = smoteResampler.fit_resample(sourceDataDummies.drop(columns = ["Attrition"], axis = 1), sourceDataDummies["Attrition"])

In [20]:
# se crea el nuevo conjunto de datos balanceado de entrenamiento
if "Attrition" not in dummyColumnNames:
    trainDataBalance = pd.DataFrame(data = smX, columns = dummyColumnNames)
    
    # se agrega la columna a predecir "Accident_Severity" para no reescribir mas codigo posteriormente
    trainDataBalance["Attrition"] = smY
    dummyColumnNames = list(sourceDataDummies)

In [21]:
trainDataBalance.dtypes

Age_18                     uint8
Age_19                     uint8
Age_20                     uint8
Age_21                     uint8
Age_22                     uint8
                           ...  
YearsWithCurrManager_14    uint8
YearsWithCurrManager_15    uint8
YearsWithCurrManager_16    uint8
YearsWithCurrManager_17    uint8
Attrition                  int64
Length: 2683, dtype: object

In [22]:
# se confirma si el balanceo de clases esta bien hecho
trainDataBalance["Attrition"].value_counts()

1    1233
0    1233
Name: Attrition, dtype: int64

### Entrenamiento Preliminar de Arboles
En esta etapa se crean 2 modelos para entrenar. El primero se denomina ingenuo porque no tiene en cuenta el desbalanceo de clase. Y el segundo, se denomina balanceo por datos porque implementa el procedimiento SMOTE para el conjunto de datos. 

Los modelos se denominan:
-	Clasificador ingenuo.
-	Clasificador SMOTE.

Estos modelos entrenados se toman como base para la optimización que posteriormente se realiza con los hiper-parámetros.

Específicamente las instrucciones para implementar estas variantes son:
- Balancear el conjunto de datos con la función smoteResampler.fit_resample().

In [23]:
# se remueve la clase a predecir
X = trainData.drop(columns = ["Attrition"], axis = 1)
XB = trainDataBalance.drop(columns = ["Attrition"], axis = 1)

In [24]:
# clase a predecir
y = trainData["Attrition"]
yB = trainDataBalance["Attrition"]

In [25]:
# division de poblacion de entrenamiento y pruebas
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size = 0.2, random_state = 42)
X_trainB, X_testB, y_trainB, y_testB = train_test_split(XB, yB, test_size = 0.2, random_state = 42)

In [26]:
classifierNaive = RandomForestClassifier(n_estimators = 100, max_depth = 2, random_state = 42)
classifierBData = RandomForestClassifier(n_estimators = 100, max_depth = 2, random_state = 42)

In [27]:
# entrenamiento de los modelo clasificador
# classifierNaive = modelo de arbol sin balanceo en datos
classifierNaive.fit(X_train, y_train)

RandomForestClassifier(bootstrap=True, class_weight=None, criterion='gini',
                       max_depth=2, max_features='auto', max_leaf_nodes=None,
                       min_impurity_decrease=0.0, min_impurity_split=None,
                       min_samples_leaf=1, min_samples_split=2,
                       min_weight_fraction_leaf=0.0, n_estimators=100,
                       n_jobs=None, oob_score=False, random_state=42, verbose=0,
                       warm_start=False)

In [28]:
# classifierBData = modelo de arbol con balanceo por conjunto de datos
classifierBData.fit(X_trainB, y_trainB)

RandomForestClassifier(bootstrap=True, class_weight=None, criterion='gini',
                       max_depth=2, max_features='auto', max_leaf_nodes=None,
                       min_impurity_decrease=0.0, min_impurity_split=None,
                       min_samples_leaf=1, min_samples_split=2,
                       min_weight_fraction_leaf=0.0, n_estimators=100,
                       n_jobs=None, oob_score=False, random_state=42, verbose=0,
                       warm_start=False)

In [29]:
# pruebas preliminares del entrenamiento ingenuo
attritionPrediction = classifierNaive.predict(X_test)

In [30]:
# pruebas preliminares del entrenamiento con balanceo por datos
attritionPredictionBData = classifierBData.predict(X_testB)

In [31]:
# validacion preliminar ingenua
naiveScore = cross_val_score(classifierNaive, X_train, y_train, cv = 3)

In [32]:
# validacion preliminar con balanceo por SMOTE
scoreBData = cross_val_score(classifierBData, X_trainB, y_trainB, cv = 3)

In [33]:
# Informe de los resultados para las pruebas ingenuas
print("----- Reporte de Pruebas Ingenuo -----")
print("--- Conteo ---\n" + str(Counter(attritionPrediction)))
print("--- Matriz de Confusion ---\n" + str(confusion_matrix(y_test, attritionPrediction)))
print("--- Reporte de Pruebas: ---")
print(classification_report(y_test, attritionPrediction))
print("--- Puntaje ---\n" + str(naiveScore))
print("--- Puntaje Promedio ---\n" + str(naiveScore.mean()))
preScore = naiveScore.mean()

----- Reporte de Pruebas Ingenuo -----
--- Conteo ---
Counter({0: 294})
--- Matriz de Confusion ---
[[255   0]
 [ 39   0]]
--- Reporte de Pruebas: ---
              precision    recall  f1-score   support

           0       0.87      1.00      0.93       255
           1       0.00      0.00      0.00        39

    accuracy                           0.87       294
   macro avg       0.43      0.50      0.46       294
weighted avg       0.75      0.87      0.81       294

--- Puntaje ---
[0.83163265 0.83163265 0.83163265]
--- Puntaje Promedio ---
0.8316326530612245


In [34]:
# Informe de los resultados para las pruebas balanceadas por los datos con SMOTE
print("----- Reporte de Pruebas Balanceado con SMOTE -----")
print("--- Conteo ---\n" + str(Counter(attritionPredictionBData)))
print("--- Matriz de Confusion ---\n" + str(confusion_matrix(y_testB, attritionPredictionBData)))
print("--- Reporte de Pruebas: ---")
print(classification_report(y_testB, attritionPredictionBData))
print("--- Puntaje ---\n" + str(scoreBData))
print("--- Puntaje Promedio ---\n" + str(scoreBData.mean()))
preScoreBData = scoreBData.mean()

----- Reporte de Pruebas Balanceado con SMOTE -----
--- Conteo ---
Counter({0: 298, 1: 196})
--- Matriz de Confusion ---
[[244   6]
 [ 54 190]]
--- Reporte de Pruebas: ---
              precision    recall  f1-score   support

           0       0.82      0.98      0.89       250
           1       0.97      0.78      0.86       244

    accuracy                           0.88       494
   macro avg       0.89      0.88      0.88       494
weighted avg       0.89      0.88      0.88       494

--- Puntaje ---
[0.88297872 0.89057751 0.88414634]
--- Puntaje Promedio ---
0.8859008574888181


### Optimización de Hiper-parámetros
En esta sección se define un espacio de optimización del modelo por medio de sus hiper-parámetros (n_estimators, max_features, max_depth, criterion). Además, se define un puntaje o método de evaluación para los modelos, aunque inicialmente se consideraron 2 alternativas del modelo de evaluación, después de experimentos preliminares se escoge el que promedia vía average = "weighted" porque no se observa un cambio en su comportamiento con el parámetro average = "macro".

Importante para acelerar el proceso de optimización:

 - En GridSearchCV.fit() incluir el parámetro n_jobs = -2, esto hace que el proceso utilice todos los Core de procesamiento excepto uno, lo cual reduce el tiempo
 - En GridSearchCV.fit() incluir el parámetro verbose = 5, esto reduce la probabilidad de bloqueos de hilos de procesamiento al obligar a la función a enviar actualizaciones de estado a la consola.

In [35]:
# hyperparametros a optimizar 
estimators = [100, 200, 400] 
features = ["auto", "sqrt", "log2"]
depths = [2, 3, 4, 5, 6]
criterions = ["gini"] #, "entropy"]

# score sin tener en cuenta los pesos
pScoreMacro = make_scorer(precision_score, average = "macro")

#score teniendo en cuenta los pesos
pScoreWeight = make_scorer(precision_score, average = "weighted")

# criterios de evaluacion por los que se quiere optimizar el modelo
scores = [pScoreMacro, pScoreWeight]

hyperParameters = {
    'n_estimators': estimators,
    'max_features': features,
    'max_depth' : depths,
    'criterion' :criterions
}

#### OPTIMIZACION DEL CLASIFICADOR INGENUO

In [36]:
# funcion que implementa el ajuste de los hyperparametros con el estimador que no tiene en cuenta el desbalanceo
searchGridResults = GridSearchCV(estimator = classifierNaive,
                     scoring = scores[1],
                     cv = 3,
                     param_grid = hyperParameters, n_jobs = -2, verbose = 5)

In [37]:
# ajusta el modelo optimizando los hyperparametros
searchGridResults.fit(X_train, y_train)

Fitting 3 folds for each of 45 candidates, totalling 135 fits


[Parallel(n_jobs=-2)]: Using backend LokyBackend with 7 concurrent workers.
[Parallel(n_jobs=-2)]: Done   4 tasks      | elapsed:    5.4s
[Parallel(n_jobs=-2)]: Done  58 tasks      | elapsed:   14.8s
[Parallel(n_jobs=-2)]: Done 135 out of 135 | elapsed:   29.8s finished


GridSearchCV(cv=3, error_score='raise-deprecating',
             estimator=RandomForestClassifier(bootstrap=True, class_weight=None,
                                              criterion='gini', max_depth=2,
                                              max_features='auto',
                                              max_leaf_nodes=None,
                                              min_impurity_decrease=0.0,
                                              min_impurity_split=None,
                                              min_samples_leaf=1,
                                              min_samples_split=2,
                                              min_weight_fraction_leaf=0.0,
                                              n_estimators=100, n_jobs=None,
                                              oob_score=False, random_state=42,
                                              verbose=0, warm_start=False),
             iid='warn', n_jobs=-2,
             param_grid={'criterio

In [38]:
# mejor resultado segun presicion
bestScore = searchGridResults.best_score_
# mejores hyperpametros segun presicion
bestParameters = searchGridResults.best_params_

#### OPTIMIZACION DEL CLASIFICADOR POR SMOTE

In [39]:
# funcion que implementa el ajuste de los hyperparametros con el estimador teniendo en cuenta peso
searchGridResultsBData = GridSearchCV(estimator = classifierBData,
                     scoring = scores[1],
                     cv = 3,
                     param_grid = hyperParameters, n_jobs = -2, verbose = 5)

In [40]:
# ajusta el modelo optimizando los hyperparametros
searchGridResultsBData.fit(X_trainB, y_trainB)

Fitting 3 folds for each of 45 candidates, totalling 135 fits


[Parallel(n_jobs=-2)]: Using backend LokyBackend with 7 concurrent workers.
[Parallel(n_jobs=-2)]: Done   4 tasks      | elapsed:    2.0s
[Parallel(n_jobs=-2)]: Done  58 tasks      | elapsed:   19.5s
[Parallel(n_jobs=-2)]: Done 135 out of 135 | elapsed:   55.6s finished


GridSearchCV(cv=3, error_score='raise-deprecating',
             estimator=RandomForestClassifier(bootstrap=True, class_weight=None,
                                              criterion='gini', max_depth=2,
                                              max_features='auto',
                                              max_leaf_nodes=None,
                                              min_impurity_decrease=0.0,
                                              min_impurity_split=None,
                                              min_samples_leaf=1,
                                              min_samples_split=2,
                                              min_weight_fraction_leaf=0.0,
                                              n_estimators=100, n_jobs=None,
                                              oob_score=False, random_state=42,
                                              verbose=0, warm_start=False),
             iid='warn', n_jobs=-2,
             param_grid={'criterio

In [41]:
# mejor resultado segun presicion
bestScoreBData = searchGridResultsBData.best_score_
# mejores hyperpametros segun presicion
bestParametersBData = searchGridResultsBData.best_params_

### RESULTADOS EXPERIMENTALES
En esta sección se crea la matriz de confusión y el informe del resto de variables de rendimiento de los modelos probados par su futuro análisis.

In [42]:
# pruebas preliminares del entrenamiento ingenuo
attritionPrediction = searchGridResults.predict(X_test)

In [43]:
# pruebas preliminares del entrenamiento con balanceo por datos
attritionPredictionBData = searchGridResultsBData.predict(X_testB)

In [44]:
# Informe de los resultados para las pruebas ingenuas optimizadas
print("----- Reporte de Pruebas Ingenuo -----")
print("Parametros Optimizados: " + str(bestParameters))
print("--- Conteo de Clasificaciones ---\n" + str(Counter(attritionPrediction)))
print("--- Matriz de Confusion ---\n" + str(confusion_matrix(y_test, attritionPrediction)))
print("--- Reporte de Pruebas: ---")
print(classification_report(y_test, attritionPrediction))
print("--- Mejor Puntaje Promedio ---\n" + str(searchGridResults.best_score_))

----- Reporte de Pruebas Ingenuo -----
Parametros Optimizados: {'criterion': 'gini', 'max_depth': 2, 'max_features': 'auto', 'n_estimators': 100}
--- Conteo de Clasificaciones ---
Counter({0: 294})
--- Matriz de Confusion ---
[[255   0]
 [ 39   0]]
--- Reporte de Pruebas: ---
              precision    recall  f1-score   support

           0       0.87      1.00      0.93       255
           1       0.00      0.00      0.00        39

    accuracy                           0.87       294
   macro avg       0.43      0.50      0.46       294
weighted avg       0.75      0.87      0.81       294

--- Mejor Puntaje Promedio ---
0.6916128696376509


In [45]:
# Informe de los resultados optimizadas para las pruebas balanceadas por los datos con SMOTE
print("----- Reporte de Pruebas Balanceado con SMOTE -----")
print("Parametros Optimizados: " + str(bestParametersBData))
print("--- Conteo de Clasificaciones ---\n" + str(Counter(attritionPredictionBData)))
print("--- Matriz de Confusion ---\n" + str(confusion_matrix(y_testB, attritionPredictionBData)))
print("--- Reporte de Pruebas: ---")
print(classification_report(y_testB, attritionPredictionBData))
print("--- Mejor Puntaje Promedio ---\n" + str(searchGridResultsBData.best_score_))

----- Reporte de Pruebas Balanceado con SMOTE -----
Parametros Optimizados: {'criterion': 'gini', 'max_depth': 5, 'max_features': 'log2', 'n_estimators': 400}
--- Conteo de Clasificaciones ---
Counter({0: 296, 1: 198})
--- Matriz de Confusion ---
[[248   2]
 [ 48 196]]
--- Reporte de Pruebas: ---
              precision    recall  f1-score   support

           0       0.84      0.99      0.91       250
           1       0.99      0.80      0.89       244

    accuracy                           0.90       494
   macro avg       0.91      0.90      0.90       494
weighted avg       0.91      0.90      0.90       494

--- Mejor Puntaje Promedio ---
0.9194085689222247


### ANÁLISIS Y CONCLUSIONES

Durante la preparación de datos, se simplifica el conjunto de entrenamiento transformando los datos categóricos de tipo String a números enteros y se crea una representación alternativa del conjunto de datos para agilizar el entrenamiento del árbol. No se discretizan las variables como edad, tiempo en la empresa y similares porque son comportamientos importantes del fenómeno y se espera predecir el retiro de los empleados con por lo menos una precisión anual.

Después en el entrenamiento preliminar de los dos modelos (ingenuo y SMOTE) se observa que el entrenamiento del árbol ingenuo no permite reconocer la clase minoritaria, en este caso en la columna “Attrition” está el sí (“Yes:0”) que significa que el empleado si se retiró de la empresa.

Por lo anterior, se ejecuta el procedimiento SMOTE para balancear el conteo dentro del conjunto de datos de entrenamiento. Como consecuencia el modelo entrenado con SMOTE tiene un mejor rendimiento y puede reconocer de manera adecuada las dos clases de interés de la atrición laboral.

Adicionalmente, durante la optimización se decidió una búsqueda ingenua por el método “GridSearchCV” y teniendo en cuenta los parámetros de numero de estimadores, características máximas para tener en cuenta, profundidad del árbol y criterio de evaluación (“n_estimators”, “max_features”, “max_depth”, “criterion” respectivamente).

En un principio el criterio de evaluación tenia dos alternativas, “gini” y “entropy” pero como el criterio de entropía se considera generalmente de menor calidad se decide utilizar solo el “gini”. Por otro lado, el tiempo de optimización del modelo es menor a 5 minutos, lo que confirma lo innecesario que es discretizar algunas variables continuas de entrenamiento.

Por último, en la optimización los resultados del árbol con SMOTE son mejores en puntaje y capacidad de distinguir las diferentes categorías (“Yes:1” y “No:0”). De nuevo en la optimización el árbol con un modelo ingenuo es incapaz de reconocer la clase minoritaria, en este caso “Yes:0”.